# 12. 이미지 변형 (원근)

## 사다리꼴 이미지 펼치기

In [1]:
import cv2
import numpy as np

img = cv2.imread('newspaper.jpg')

width, height = 640, 240 # 가로 크기 640, 세로 크기 240 으로 결과물 출력

src = np.array([[511, 352], [1008, 345], [1122, 584], [455, 594]], dtype=np.float32) # Input 4개 지점
dst = np.array([[0, 0], [width, 0], [width, height], [0, height]], dtype=np.float32) # Output 4개 지점
# input과 output은 1대1 매칭
# 좌상, 우상, 우하, 좌하 (시계 방향으로 4 지점 정의)

matrix = cv2.getPerspectiveTransform(src, dst) # Matrix 얻어옴
result = cv2.warpPerspective(img, matrix, (width, height)) # matrix 대로 변환을 함

cv2.imshow('img', img)
cv2.imshow('result', result)
cv2.waitKey(0)
cv2.destroyAllWindows()

## 회전된 이미지 올바로 세우기

예제 이미지 : https://pixabay.com/images/id-682332/  
크기 : 1280 x 1019  
파일명 : poker.jpg

In [3]:
import cv2
import numpy as np

img = cv2.imread('poker.jpg')

width, height = 530, 710

src = np.array([[702, 143], [1133, 414], [726, 1007], [276, 700]], dtype=np.float32) # Input 4개 지점
dst = np.array([[0, 0], [width, 0], [width, height], [0, height]], dtype=np.float32) # Output 4개 지점
# 좌상, 우상, 우하, 좌하 (시계 방향으로 4 지점 정의)

matrix = cv2.getPerspectiveTransform(src, dst) # Matrix 얻어옴
result = cv2.warpPerspective(img, matrix, (width, height)) # matrix 대로 변환을 함

cv2.imshow('img', img)
cv2.imshow('result', result)
cv2.waitKey(0)
cv2.destroyAllWindows()

## 미니 프로젝트 : 반자동 문서 스캐너

### 마우스 이벤트 등록

In [11]:
import cv2

def mouse_handler(event, x, y, flags, param):
    if event == cv2.EVENT_LBUTTONDOWN: # 마우스 왼쪽 버튼 Down
        print('왼쪽 버튼 Down')
        print(x, y)
    elif event == cv2.EVENT_LBUTTONUP: # 마우스 왼쪽 버튼 Up
        print('왼쪽 버튼 Up')
        print(x, y)
    elif event == cv2.EVENT_LBUTTONDBLCLK: # 마우스 왼쪽 버튼 더블 클릭
        print('왼쪽 버튼 Double Click')
#     elif event == cv2.EVENT_MOUSEMOVE: # 마우스 이동
#         print('마우스 이동')
    elif event == cv2.EVENT_RBUTTONDOWN: # 오른쪽 버튼 Down
        print('오른쪽 버튼 Down')

img = cv2.imread('poker.jpg')
cv2.namedWindow('img') # img 란 이름의 윈도우를 먼저 만들어두는 것. 여기에 마우스 이벤트를 처리하기 위한 핸들러 적용
cv2.setMouseCallback('img', mouse_handler)
cv2.imshow('img', img)
cv2.waitKey(0)
cv2.destroyAllWindows()

왼쪽 버튼 Down
339 400
왼쪽 버튼 Up
339 400
왼쪽 버튼 Double Click
왼쪽 버튼 Up
339 400
오른쪽 버튼 Down


### 프로젝트

In [28]:
import cv2
import numpy as np

point_list = []
src_img = cv2.imread('poker.jpg')
src_img = cv2.resize(src_img, None, fx=0.5, fy=0.5) # 이미지가 너무 커서 0.5 배로 축소

COLOR = (255, 0, 255) # 핑크
THICKNESS = 2
drawing = False # 선을 그릴지 여부

def mouse_handler(event, x, y, flags, param):
    global drawing
    dst_img = src_img.copy()
    
    if event == cv2.EVENT_LBUTTONDOWN: # 마우스 왼쪽 버튼 Down -> 선그리기시작, 위치저장 -> 원그리기
        drawing = True # 선을 그리기 시작
        point_list.append((x, y))
     
    if drawing:
        prev_point = None # 직선의 시작점
        for point in point_list:
            cv2.circle(dst_img, point, 10, COLOR, cv2.FILLED)
            if prev_point:
                cv2.line(dst_img, prev_point, point, COLOR, THICKNESS, cv2.LINE_AA)
            prev_point = point
        
        next_point = (x, y)
        if len(point_list) == 4:
            show_result() # 결과 출력
            next_point = point_list[0] # 첫 번째 클릭한 지점
            
        cv2.line(dst_img, prev_point, next_point, COLOR, THICKNESS, cv2.LINE_AA)
        
    cv2.imshow('img', dst_img)
    
def show_result():
    width, height = 530 // 2, 710 // 2 # 이미지가 너무 커서 0.5 배로 축소
    src = np.float32(point_list)
    dst = np.array([[0, 0], [width, 0], [width, height], [0, height]], dtype=np.float32) # Output 4개 지점
    # 좌상, 우상, 우하, 좌하 (시계 방향으로 4 지점 정의)

    matrix = cv2.getPerspectiveTransform(src, dst) # Matrix 얻어옴
    result = cv2.warpPerspective(src_img, matrix, (width, height)) # matrix 대로 변환을 함
    cv2.imshow('result', result)

cv2.namedWindow('img') # img 란 이름의 윈도우를 먼저 만들어두는 것. 여기에 마우스 이벤트를 처리하기 위한 핸들러 적용
cv2.setMouseCallback('img', mouse_handler)
cv2.imshow('img', src_img)
cv2.waitKey(0)
cv2.destroyAllWindows()

# 새창->마컨(클릭,좌표)->이미지->좌표 원->전좌표 선-> 좌표길이 선 -> 새창 너비높이inputooutput->gptwps

# 새로운 창 만들기 -> 새로운창에 마우스컨트롤러 만들기 -> 이미지 불러오기 -> 클릭이벤트+좌표 -> 좌표리스트 + 원그리기 
# -> 이전좌표저장 + 선그리기 -> 리스트 길이 제한 + 결과출력 -> 너비,높이,input,output -> gptwps